In [1]:
import xarray as xr, numpy as np
from bmi_topography import Topography as topography
from skimage.transform import resize, rescale
import pathlib, yaml
from joblib import Parallel, delayed
import orographicRainLinearTheory as lt

In [2]:
with open('../input.yml') as f:
    input_data = yaml.load(f, Loader=yaml.loader.SafeLoader)

In [3]:
study_area = input_data['study_area']
lat_south = input_data['study_area_bounds']['lat_south']
lat_north = input_data['study_area_bounds']['lat_north']
lon_west = input_data['study_area_bounds']['lon_west']
lon_east = input_data['study_area_bounds']['lon_east']

year_range = sorted(list(range(input_data['training_period']['start'], input_data['training_period']['end']+1)) + \
                    list(range(input_data['validation_period']['start'], input_data['validation_period']['end']+1)) + \
                    list(range(input_data['testing_period']['start'], input_data['testing_period']['end']+1)))

out_dir = pathlib.Path(input_data['data_directories']['output']).joinpath(input_data['study_area'], 'physics_linear_sr')
out_dir.mkdir(parents=True, exist_ok=True)

in_dir = pathlib.Path(input_data['data_directories']['output']).joinpath(input_data['study_area'], 'input_data')
in_extra_dir = pathlib.Path(input_data['data_directories']['output']).joinpath(input_data['study_area'], 'input_data_extra')

In [5]:
u = xr.open_dataset(in_extra_dir/'era5_u_wind.nc')
v = xr.open_dataset(in_extra_dir/'era5_v_wind.nc')
lsp = xr.open_dataset(in_extra_dir/'era5_large_scale_rainfall.nc')
tp_lr = xr.open_dataset(in_extra_dir/'era5_rainfall.nc')
tp_hr = xr.open_dataset(in_dir/'era5_land_rainfall.nc')
tp_hr_extra = xr.open_dataset(in_extra_dir/'era5_land_rainfall.nc')
tp_hr_extra = tp_hr_extra.where((tp_hr_extra.lat > lat_south-0.5) & (tp_hr_extra.lat < lat_north+0.5) & (tp_hr_extra.lon < lon_east+0.5)  & (tp_hr_extra.lon > lon_west-0.5), drop=True)
ts = xr.open_dataset(in_dir/'era5_temperature.nc')
ps = xr.open_dataset(in_dir/'era5_pressure.nc')

In [ ]:
def interp_wind(lr, hr_lat, hr_lon):
    hr = lr.interp(lat=hr_lat, lon=hr_lon, method="cubic")
    return hr

def interp_rain(lr, hr_lat, hr_lon):
    hr = lr.interp(lat=hr_lat, lon=hr_lon, method="cubic")
    return hr

def interp_temp(lr, hr_lat, hr_lon):
    hr = lr.interp(lat=hr_lat, lon=hr_lon, method="linear", kwargs={"fill_value": "extrapolate"})
    return hr

def interp_pressure(lr, hr_lat, hr_lon):
    hr = lr.interp(lat=hr_lat, lon=hr_lon, method="linear", kwargs={"fill_value": "extrapolate"})
    return hr

In [ ]:
wind_lat = tp_hr_extra.lat.sel(lat=slice(lat_north, lat_south)).values
wind_lon = tp_hr_extra.lon.sel(lon=slice(lon_west, lon_east)).values

In [ ]:
ui = np.array(Parallel(n_jobs=30)(delayed(interp_wind)(ut, wind_lat, wind_lon) for ut in u.u_wind))
vi = np.array(Parallel(n_jobs=30)(delayed(interp_wind)(vt, wind_lat, wind_lon) for vt in v.v_wind))
lspi = np.array(Parallel(n_jobs=30)(delayed(interp_rain)(lspt, wind_lat, wind_lon) for lspt in lsp.rainfall))
tsi = np.array(Parallel(n_jobs=30)(delayed(interp_temp)(tt, wind_lat, wind_lon) for tt in ts.temperature))
psi = np.array(Parallel(n_jobs=30)(delayed(interp_pressure)(pst, wind_lat, wind_lon) for pst in ps.pressure))

In [ ]:
gamma_m = lt.find_saturated_moist_adiabatic_lapse_rate(tsi, psi)
gamma = 0.99 * gamma_m

In [ ]:
local_topography = topography(dem_type='SRTMGL1', south=lat_south-0.5, north=lat_north+0.5, west=lon_west-0.5, east=lon_east+0.5, output_format='GTiff')
local_topography.fetch()
dem = local_topography.load()
mx = dem.x[int(np.size(dem.x)/2)].values
my = dem.y[int(np.size(dem.y)/2)].values

In [ ]:
scale_factor_5l = 360
dx_5l = lt.haversine(my, mx, my, dem.x[int(np.size(dem.x)/2+1)].values) * scale_factor_5l
dy_5l = lt.haversine(my, mx, dem.y[int(np.size(dem.y)/2+1)].values, mx) * scale_factor_5l
h_5l = rescale(np.squeeze(dem.values), 1/scale_factor_5l, anti_aliasing=False)

In [ ]:
scale_factor_5 = 360*2.5
dx_5 = lt.haversine(my, mx, my, dem.x[int(np.size(dem.x)/2+1)].values) * scale_factor_5
dy_5 = lt.haversine(my, mx, dem.y[int(np.size(dem.y)/2+1)].values, mx) * scale_factor_5
h_5 = rescale(np.squeeze(dem.values), 1/scale_factor_5, anti_aliasing=False)

In [ ]:
w = np.empty([np.shape(ui)[1], np.shape(ui)[2]])
for j in range(np.shape(ui)[1]):
    for i in range(np.shape(ui)[2]):
        w[j, i] = 1/(lt.haversine(my, mx, wind_lat[j], wind_lon[i])**2)
wn = w / np.sum(w)
wn2 = np.repeat(np.repeat(wn[:, :, np.newaxis], np.shape(h_5l)[0], axis=2)[:, :, :, np.newaxis], np.shape(h_5l)[1], axis=3)

In [ ]:
ua = np.average(np.array(ui).reshape(np.shape(ui)[0], -1), weights=wn.ravel(), axis=-1)
va = np.average(np.array(vi).reshape(np.shape(vi)[0], -1), weights=wn.ravel(), axis=-1)

In [ ]:
tauc = 900
tauf = 900

In [ ]:
def calculate_orographic_rain_5l(d):
    p = lt.compute_orographic_rain(h_5l, ua[d], va[d], np.mean(np.ravel(tsi[d, ...])), np.mean(np.ravel(psi[d, ...])), np.mean(np.ravel(gamma[d, ...])), tauc, tauf, dx_5l, dy_5l) 
    p = p*3600*24
    return np.squeeze(p)[5:-5, 5:-5]

def calculate_orographic_rain_5(d):
    p = lt.compute_orographic_rain(h_5, ua[d], va[d], np.mean(np.ravel(tsi[d, ...])), np.mean(np.ravel(psi[d, ...])), np.mean(np.ravel(gamma[d, ...])), tauc, tauf, dx_5, dy_5) 
    return np.squeeze(p*3600*24)

In [ ]:
rain_5l_topo_linear = np.array(Parallel(n_jobs=30)(delayed(calculate_orographic_rain_5l)(d) for d in range(np.shape(ui)[0])))
rain_5_topo_linear = np.array(Parallel(n_jobs=30)(delayed(calculate_orographic_rain_5)(d) for d in range(np.shape(ui)[0])))

In [ ]:
tp_lr_ls = tp_lr.rainfall[:,2:-2,2:-2] - rain_5_topo_linear
tpi = np.array(Parallel(n_jobs=30)(delayed(interp_rain)(pt, wind_lat, wind_lon) for pt in tp_lr_ls))
sr_ph = tpi + rain_5l_topo_linear
sr_ph[sr_ph<0] = 0

In [ ]:
with xr.open_dataset(in_dir/'era5_land_rainfall.nc') as ds1:

    ds = xr.Dataset(
        data_vars=dict(rainfall=(["time", "lon", "lat"], np.squeeze(sr_ph))),
        coords=dict(lon=ds1.lon.data, lat=ds1.lat.data, time=ds1.time),
        attrs=dict(description="ERA5 daily rainfall downscaled with Linear Method (Spectral)"),
    )

    ds.to_netcdf(out_dir/"era5_sr1.nc")

In [ ]:
with xr.open_dataset(in_dir/'era5_land_rainfall.nc') as ds1:

    ds = xr.Dataset(
        data_vars=dict(rainfall=(["time", "lon", "lat"], np.squeeze(rain_5l_topo_linear))),
        coords=dict(lon=ds1.lon.data, lat=ds1.lat.data, time=ds1.time),
        attrs=dict(description="Orographic Rainfall (ERA5 Land Resolution)"),
    )

    ds.to_netcdf(out_dir/"era5_land_topo.nc")

In [ ]:
with xr.open_dataset(in_dir/'era5_rainfall.nc') as ds1:

    ds = xr.Dataset(
        data_vars=dict(rainfall=(["time", "lon", "lat"], np.squeeze(rain_5_topo_linear[:,2:-2,2:-2]))),
        coords=dict(lon=ds1.lon.data, lat=ds1.lat.data, time=ds1.time),
        attrs=dict(description="Orographic Rainfall (ERA5 Resolution)"),
    )

    ds.to_netcdf(out_dir/"era5_topo.nc")